# Imports

In [76]:
import qgrid, datetime, requests, os, threading, concurrent.futures, sys
import numpy as np, pandas as pd

import plotly.express       as px
import plotly.graph_objects as go
import plotly.io            as pio
from plotly.subplots        import make_subplots
from tqdm.notebook          import tqdm
from dotenv                 import load_dotenv

load_dotenv('./.env')
sys.path.append(os.path.abspath(os.path.join('../../tapcap/data')))
from tools.mapping          import Mapping
from tools.financial_tools  import c

pio.templates.default = "plotly_white"
px.set_mapbox_access_token(os.environ["MAPBOX_TOKEN"])
gm = Mapping()

In [5]:
acris = pd.read_excel('acris.xlsx')
doc   = pd.read_excel('doc_detail.xlsx')

https://data.cityofnewyork.us/widgets/7isb-wh4c

# Acris EDA

## Joining the two files

There are two files provided to us, an export from acris (`acris.xlsx`) and and document detail table (`doc_detail`). From a preliminary look, it appears the `acris` table contains information about the transaction parties, the transaction type, and a reference id to the documents associated to the transaction. The `doc_detail` table, in turn, gives us information on the relevant dates and dollar amounts in the referenced documents. 

We can join the two tables via `doc_id`, however it seems many records do not match (~35% match). This likely indicates that the files are just sample exports. 38k records should be sufficient for some inital exploratory data analysis.

In [6]:
acris.head()

BOROUGH  BLOCK  LOT            DOC_ID         DOCUMENT_TYPE  \
0        1      2    2  2019071100419003  ASSIGNMENT, MORTGAGE   
1        1      2    2  2019071100419003  ASSIGNMENT, MORTGAGE   
2        1      2    2  2019071100419020  ASSIGNMENT, MORTGAGE   
3        1      2    2  2019071100419020  ASSIGNMENT, MORTGAGE   
4        1      2    2  2019071100419021  ASSIGNMENT, MORTGAGE   

            PARTY_TYPE  SEQ                                            NAME  \
0  ASSIGNEE/NEW LENDER    1                      ACORE CAPITAL MORTGAGE, LP   
1  ASSIGNOR/OLD LENDER    1                     10 SOUTH STREET FUNDING LLC   
2  ASSIGNEE/NEW LENDER    1                             10 SOUTH STREET LLC   
3  ASSIGNOR/OLD LENDER    1               10 SOUTH STREET MASTER TENANT LLC   
4  ASSIGNEE/NEW LENDER    1  NEW YORK CITY ECONOMIC DEVELOPMENT CORPORATION   

                                     ADDR1                        ADDR2  \
0  80 E. SIR FRANCIS DRAKE BLVD., SUITE 2A                          NaN   
1                    C/O: MIDTOWN EQUITIES  141 FIFTH AVENUE, 2ND FLOOR   
2                 C/O MIDTOWN EQUITIES LLC  141 FIFTH AVENUE, 2ND FLOOR   
3                 C/O MIDTOWN EQUITIES LLC  141 FIFTH AVENUE, 2ND FLOOR   
4                       110 WILLIAM STREET                          NaN   

  COUNTRY      CITY STATE    ZIP  
0      US  LARKSPUR    CA  94939  
1      US  NEW YORK    NY  10010  
2      US  NEW YORK    NY  10010  
3      US  NEW YORK    NY  10010  
4      US  NEW YORK    NY  10038

In [7]:
doc.head()

DOC_ID DOC_TYPE DOCUMENT_DATE  DOCUMENT_AMT FEDTAX_SERIAL_NBR  \
0  FT_3690001546769      SAT           NaT           0.0               NaN   
1  FT_3690001536469     ASST           NaT           0.0               NaN   
2  FT_3690001587269     DEED    1990-12-13           0.0               NaN   
3  FT_3690001591069     ASST           NaT           0.0               NaN   
4  FT_3690001550969     ASST           NaT           0.0               NaN   

  FEDTAX_ASSESSMENT_DATE UCC_COLLATERAL RECORDED_DATETIME  RECORDED_BOROUGH  \
0                    NaT            NaN        1990-06-14                 3   
1                    NaT            NaN        1990-05-07                 3   
2                    NaT            NaN        1990-12-14                 3   
3                    NaT            NaN        1991-01-08                 3   
4                    NaT            NaN        1990-07-06                 3   

  EXPIRATION_DATE  CRFN  RPTT_NBR  REEL_YR  REEL_NBR  REEL_PG FILE_NBR  \
0             NaN   NaN       NaN   1990.0    2570.0    434.0      NaN   
1             NaN   NaN       NaN   1990.0    2550.0   1058.0      NaN   
2             NaN   NaN   17123.0   1990.0    2646.0   2335.0      NaN   
3             NaN   NaN       NaN   1991.0    2654.0    769.0      NaN   
4             NaN   NaN       NaN   1990.0    2578.0   1493.0      NaN   

   MAP_SEQ_NBR  MORTGAGE_TAX_AMT  
0          0.0               0.0  
1          0.0               0.0  
2          0.0               0.0  
3          0.0               0.0  
4          0.0               0.0

In [8]:
n_records_acris  = len(acris)
n_records_docs   = len(doc)
n_records_merged = len(acris.merge(doc, on='DOC_ID'))

f'{n_records_acris} acris records. {n_records_docs} document detail records. {n_records_merged} ({n_records_merged*100/n_records_docs:.2f}% of docs) records in common'

'111967 acris records. 1048575 document detail records. 38771 (3.70% of docs) records in common'

In [9]:
acris = acris.merge(doc, on='DOC_ID')

acris['EXPIRATION_DATE'] = pd.to_datetime(acris['EXPIRATION_DATE'], errors='coerce')
acris['DOCUMENT_DATE']   = pd.to_datetime(acris['DOCUMENT_DATE'], errors='coerce')

In [10]:
acris.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 38771 entries, 0 to 38770
Data columns (total 31 columns):
 #   Column                  Non-Null Count  Dtype         
---  ------                  --------------  -----         
 0   BOROUGH                 38771 non-null  int64         
 1   BLOCK                   38771 non-null  int64         
 2   LOT                     38771 non-null  int64         
 3   DOC_ID                  38771 non-null  object        
 4   DOCUMENT_TYPE           38771 non-null  object        
 5   PARTY_TYPE              38771 non-null  object        
 6   SEQ                     38771 non-null  int64         
 7   NAME                    38771 non-null  object        
 8   ADDR1                   37378 non-null  object        
 9   ADDR2                   12292 non-null  object        
 10  COUNTRY                 37615 non-null  object        
 11  CITY                    37378 non-null  object        
 12  STATE                   37341 non-null  object

## Types and Parties

Digging into the document types and parties transacting, we immediately see a very long tail of transaction parties. The top 25 parties make up ~26% of the records, with NYCB JPM, CapOne and Signature in the lead. Most recorded documents here are mortgages and agreemnts (and given the problem were trying to solve, of course this is the extract). 

In [37]:
# correct Mortgagor misspelling and other fixes
party_changes = {
    'MORTGAGER/BORROWER': 'MORTGAGOR/BORROWER',
    'MORTGAGOR'         : 'MORTGAGOR/BORROWER',
    'MORTGAGEE'         : 'MORTGAGEE/LENDER',
    'ASSIGNOR'          : 'ASSIGNOR/OLD LENDER',
    'ASSIGNEE'          : 'ASSIGNEE/NEW LENDER',
    'PARTY ONE/MORTGAGOR' : 'MORTGAGOR/BORROWER',
    'PARTY TWO/MORTGAGEE' : 'MORTGAGEE/LENDER',
}

acris['PARTY_TYPE'] = acris['PARTY_TYPE'].replace(party_changes)

In [38]:
# Number of Unique Parties
acris['NAME'].nunique()

10665

In [39]:
# Number of Unique Documents
acris['DOC_ID'].nunique()

13383

In [40]:
px.bar(acris['DOCUMENT_TYPE'].value_counts(), title='Count of Document Types')

In [41]:
px.bar(acris['PARTY_TYPE'].value_counts(), title='Count of Party Types')

In [17]:
# % of Total records owned by top N parties
n = 25
len(acris[acris['NAME'].isin(acris['NAME'].value_counts()[:n].index)])/len(acris)

0.2632379871553481

In [18]:
fig = px.bar(acris['NAME'].value_counts()[:25], title='Top 25 Parties by Record Count')
fig.update_layout(xaxis={'tickangle':45}, margin={'l':0, 'r':0, 't':50, 'b':200})

In [19]:
# Top N for each party type
n = 10
top_by_party = acris.groupby('PARTY_TYPE').agg({
   'NAME': lambda x: '|'.join([f'{l} - {c}' for l, c in zip(x.value_counts().index[:n], x.value_counts()[:n])])
})

fig = make_subplots(
    rows=len(top_by_party)//2, 
    cols=2,
    subplot_titles=top_by_party.index
)

for i, party_type in enumerate(top_by_party.index):
    partiers = top_by_party.loc[party_type].values[0].split('|')
    records = np.array([[name, cnt] for entity in partiers for name, cnt in [entity.split(' - ')]])
    x, y = records[:,0], records[:,1]
    
    
    fig.add_trace(
        go.Bar(x=x, y=y),
        row=i//2 + 1, col=i%2 + 1
    )


fig.update_layout(height=1800, width=1600, title_text=f"Top {n} Parties per Type")
fig.show()

Not really sure what to make of `Party 1` and `Party 2`. It could be fitting for the fields to indicate *mortgagor* and *morgagee* or *assigner* & *assignee*. There are relatively few records with the designation, so perhaps its best not to assume and ignore for now.

## Location

BBL isn't very helpful for mapping, so I called the nyc map API to gt a street address and usd google's map API to convert to lat/lng. 

It appears the sites are pretty well scattered, but some large concenrations in:

**Manhattan**:
- Harlem
- Midtown

**Bronx**
- Fordham
- Norwood

**Brooklyn**
- Prospect Park
- Downtown

1 = Manhattan
2 = Bronx
3 = Brooklyn
4 = Queens

In [11]:
acris['BOROUGH'] = acris['BOROUGH'].replace({
    1: 'Manhattan',
    2: 'Bronx',
    3: 'Brooklyn',
    4: 'Queens'
})

In [12]:
acris['LOT'].nunique()

370

In [13]:
acris['BLOCK'].nunique()

3260

In [14]:
px.bar(acris['BOROUGH'].value_counts(), title='Count of Record by Borough')

In [24]:
def google_standardize(key, address):
        '''
        Given an address string, lookup google standardized address.
        Params:
            address (str): string address to search
            incl_coords (bool): whether to include lat/lng coords in 
            returned results. Defaults to true.
        '''
        geocoding_url = 'https://maps.googleapis.com/maps/api/geocode/json'
        params = {
            'address': address,
            'key'    : os.environ['GMAP_API_KEY']
        }
        results = requests.get(geocoding_url, params=params).text
        results = json.loads(results)['results']

        if len(results) == 0:
            return {
                'op'   : 'google',
                'key'  : key,
                'data' : None
            }
        
        formatted_address = results[0]['formatted_address']

        lat = results[0]['geometry']['location']['lat']
        lng = results[0]['geometry']['location']['lng']

        return {
            'op'   : 'google',
            'key'  : key,
            'data' : (lat, lng, formatted_address)
        }

def bbl_to_address(key, borough, block, lot):
    '''
    Converts a BBL to a google standard address
    inputs:
        borough: str, ['manhattan', 'bronx', 'brooklyn', 'queens']
        block: int
        lot: int
    returns:
        tuple (lat, lng, formatted_address)
        where:
            lat: flt
            lng: flt
            formatted_address: str
    '''
    # For individual lookups: https://a836-pts-access.nyc.gov/care/Datalets/Datalet.aspx?sIndex=2&idx=1
    # Get string address from maps.nyc.gov given BBL
    
    url = 'https://maps.nyc.gov/geoclient/v1/bbl.json'

    params = {
        'borough': borough.lower(),
        'block'  : block,
        'lot'    : lot,
        'app_id' : os.environ["NYC_MAPS_APP_ID"],
        'app_key': os.environ["NYC_MAPS_APP_KEY"]
    }

    r = requests.get(url, params=params)

    try:
        bbl_response   = r.json()['bbl']

        if 'giHighHouseNumber1' in bbl_response.keys():
            street_number = bbl_response['giHighHouseNumber1']
            street_name   = bbl_response['giStreetName1']
        else:
            street_number = bbl_response['giHighHouseNumber2']
            street_name   = bbl_response['giStreetName2']


        address_string = f"{street_number} {street_name}, {borough}, NY"

        return {
            'op'  : 'bbl',
            'key' : key,
            'data': (borough, block, lot, address_string)
        }
    except:
        return {
            'op'  : 'bbl',
            'key' : key,
            'data': (borough, block, lot, None)
        }
    
def multitask_this(func, data, n_threads=3, checkpoint_after_n_rounds=100, save_func=None):
    results = {}
    
    p_bar = tqdm(total=len(data))
    with concurrent.futures.ThreadPoolExecutor(max_workers=n_threads) as executor:
        cur_idx = 0
        futures = []
        p_bar.update(1)
    
        # Initial thread send
        for n in range(n_threads):
            results[cur_idx] = data[cur_idx]
            futures.append(executor.submit(func, *(cur_idx, *data[cur_idx])))
            cur_idx += 1
    
        # as threads come in, process result and resend
        while len(futures) > 0:
            # Loop through futures and process if f.done()
            for ix, f in enumerate(futures):
                if f.done():
                    
                    #checkpoint result
                    if (cur_idx+1)%checkpoint_after_n_rounds == 0:
                        pd.DataFrame.from_dict(results, orient='index').to_csv(f'./checkpoint_{ix}.csv')
                
                    #remove from futures queue
                    del futures[ix]
                
                    #process this thing
                    res  = f.result()

                    if res['op'] == 'bbl':
                        # Got address from BBL, send to Google
                        borough, block, lot, address = res['data']
                        if address is not None:
                            futures.append(executor.submit(save_func, *(res['key'], address)))
                            continue
                        else:
                            results[res['key']] = [*results[res['key']] , 'Not Found']
                        
                    elif res['op'] == 'google':
                        # Save to results
                        results[res['key']] = [*results[res['key']] , *res['data']]
                        p_bar.update(1)
                        
                        # resend thread
                        if cur_idx < len(data):
                            results[cur_idx] = data[cur_idx]
                            futures.append(executor.submit(func, *(cur_idx, *data[cur_idx])))
                            cur_idx += 1


    pd.DataFrame.from_dict(results, orient='index').to_csv(f'./final.csv')
    return results


In [15]:
if os.path.isfile('./bbl_addr.csv'):
    bbl_addr = pd.read_csv('./bbl_addr.csv')
    bbl_addr = bbl_addr.set_index(['borough', 'block', 'lot'])
else:
    bbl_list  = acris.loc[~acris.duplicated(subset=['BOROUGH', 'BLOCK', 'LOT']), ['BOROUGH', 'BLOCK', 'LOT']].values
    n_threads = 100
    results = multitask_this(bbl_to_address, bbl_list, n_threads=n_threads, checkpoint_after_n_rounds=500, save_func=google_standardize)
    
    # This part of the code hasn't been implemented. Basically rename the final.csv to bbl_addr.csv and rerun

In [16]:
gm.map_points(bbl_addr.loc[~bbl_addr['lng'].isna(), ['lat', 'lng']].astype(float).values, heat_map=True, map_type='ROADMAP')

Figure(layout=FigureLayout(height='420px'))

In [20]:
# merge lat/lng back into acris
acris = acris.set_index(['BOROUGH', 'BLOCK', 'LOT'], drop=False)
acris.index = acris.index.set_names(['borough', 'block', 'lot'])
acris = acris.merge(bbl_addr[['lat', 'lng', 'address']], left_index=True, right_index=True, how='left')

In [68]:
# Map of top 15 lenders
top_15_lenders = acris.loc[(acris['PARTY_TYPE'].isin(['ASSIGNEE/NEW LENDER', 'MORTGAGEE/LENDER'])),'NAME'].value_counts()[:15].index

mtg_locations = acris.loc[
    (acris['PARTY_TYPE'].isin(['ASSIGNEE/NEW LENDER', 'MORTGAGEE/LENDER'])) & \
    (acris['NAME'].isin(top_15_lenders)) & \
    (~acris['lng'].isna()), 
    ['NAME', 'DOCUMENT_AMT', 'lat', 'lng']
]
mtg_locations['currency'] = mtg_locations['DOCUMENT_AMT'].apply(c)
mtg_locations['lat'] = mtg_locations['lat'].astype(float)

In [92]:
fig = px.scatter_mapbox(
    mtg_locations, 
    lat='lat',
    lon='lng',
    color="NAME", # which column to use to set the color of markers
    hover_name="currency", # column added to hover information.
    zoom=11
)
fig.update_layout(width=1600, height=1000, margin={'l':0, 'r': 0}, title='Map of Mortgages by Lender')

In [93]:
fig.write_html("./lender_map.html")

## Dates

Most of our documents (which are largely mortgage notes) are dated 2003 and future. an even larger slice is between 2010 and on, which makes sense given that most mortgages are ten year notes.

Just out of curiosity, what were those pre-1980 docs still hanging around? Turns out to be some old mortgage notes for/from ConEd and First National (and a few others)... 

In [27]:
px.histogram(acris['DOCUMENT_DATE'], title='Document Dates')

In [28]:
acris.loc[acris['DOCUMENT_DATE']< '1980-01-01', 'NAME'].value_counts()[:50]

CITY OF NY                                12
CONSOLIDATED EDISON CO OF NEW YORK INC    11
CONSOLIDATED EDISON CO OF NY INC          10
FIRST NATL CITY BK TR                      8
FIRST NATL CITY BK (TR)                    7
FIRST NATL CITY BK                         7
FIRST NAT'L CITY BK (TR)                   6
FIRST NATL CITY BANK (TR)                  6
FIRST NATL CITY BK (TRUSTEE)               6
CON ED CO OF NY INC                        6
FIRST NATL CITY BANK TR                    6
FIRST NATL CITY BK TRUSTEE                 5
CON ED CO NY INC                           5
FIRST NATIONAL CITY BANK AS TRUSTEE        5
CONSOLIDATED EDISON CO OF N Y INC          5
NEW YORK CITY                              5
CITY OF NEW YORK                           5
SCAIPATIORE REALTY CORP                    5
CON EDISON CO OF NY INC                    4
FIRST NATIONAL CITY BANK                   4
FIRST NAT CITY BK (TR)                     4
CONSOLIDATED EDISON CO NY INC              4
BHM REALTY

In [29]:
acris.loc[acris['DOCUMENT_DATE']< '1980-01-01', 'DOCUMENT_TYPE'].value_counts()

MORTGAGE    701
Name: DOCUMENT_TYPE, dtype: int64

## Dollar Figures

Keeping in mind that most doc types were mortgages, they came with the associated mortgage aamount (presumably). Most mortgage notes seem to be for under a 1.2 million, which is odd. This might be due to the data extract - perhaps there was a sort and we're just seeing the lower end? 

It seems the amounts in the agreement docs are in general more than the mortgage notes. Are the agreement docs the purchase & sale agreements? This would then make sense especially since the mtg amount is typically 20% - 40% of the amount (amortized?)

In [30]:
px.bar(acris.loc[acris['DOCUMENT_AMT']> 0, 'DOCUMENT_TYPE'].value_counts(), title='Documents with a $ amount')

In [31]:
px.bar(acris.loc[acris['MORTGAGE_TAX_AMT']> 0, 'DOCUMENT_TYPE'].value_counts(), title='Documents with a Tax $ amount')

In [32]:
# Graphing $ amounts per doc
fig = go.Figure()
nbins = 25
fig.update_layout(title='Dollar Amounts per Doc Type (<.99 pctl)')
fig.add_trace(
    go.Histogram(
        x = doc.loc[
            (doc['DOC_TYPE'] == 'MTGE') &
            (doc['DOCUMENT_AMT']>0) & 
            (doc['DOCUMENT_AMT'] <= doc['DOCUMENT_AMT'].quantile(.99)    
        ), 'DOCUMENT_AMT'],
        histnorm='percent',
        nbinsx=nbins,
        name='MTGE'
    )
)
fig.add_trace(
    go.Histogram(
        x = doc.loc[
            (doc['DOC_TYPE'] == 'AGMT') &
            (doc['DOCUMENT_AMT']>0) & 
            (doc['DOCUMENT_AMT'] <= doc['DOCUMENT_AMT'].quantile(.99)    
        ), 'DOCUMENT_AMT'],
        histnorm='percent',
        nbinsx=nbins,
        name='AGMT'
    )
)
fig.add_trace(
    go.Histogram(
        x = doc.loc[
            (doc['DOC_TYPE'] == 'AL&R') &
            (doc['DOCUMENT_AMT']>0) & 
            (doc['DOCUMENT_AMT'] <= doc['DOCUMENT_AMT'].quantile(.99)    
        ), 'DOCUMENT_AMT'],
        histnorm='percent',
        nbinsx=nbins,
        name='AL&R'
    )
)
fig.show()

In [33]:
# Graphing Tax $ amounts per doc
fig = go.Figure()
nbins = 25
fig.update_layout(title='Tax Dollar Amounts per Doc Type (<.99 pctl)')
fig.add_trace(
    go.Histogram(
        x = doc.loc[
            (doc['DOC_TYPE'] == 'MTGE') &
            (doc['MORTGAGE_TAX_AMT']>0) & 
            (doc['MORTGAGE_TAX_AMT'] <= doc['MORTGAGE_TAX_AMT'].quantile(.99)    
        ), 'MORTGAGE_TAX_AMT'],
        histnorm='percent',
        nbinsx=nbins,
        name='MTGE'
    )
)
fig.add_trace(
    go.Histogram(
        x = doc.loc[
            (doc['DOC_TYPE'] == 'AGMT') &
            (doc['MORTGAGE_TAX_AMT']>0) & 
            (doc['MORTGAGE_TAX_AMT'] <= doc['MORTGAGE_TAX_AMT'].quantile(.99)    
        ), 'MORTGAGE_TAX_AMT'],
        histnorm='percent',
        nbinsx=nbins,
        name='AGMT'
    )
)
fig.add_trace(
    go.Histogram(
        x = doc.loc[
            (doc['DOC_TYPE'] == 'AL&R') &
            (doc['MORTGAGE_TAX_AMT']>0) & 
            (doc['MORTGAGE_TAX_AMT'] <= doc['MORTGAGE_TAX_AMT'].quantile(.99)    
        ), 'MORTGAGE_TAX_AMT'],
        histnorm='percent',
        nbinsx=nbins,
        name='AL&R'
    )
)
fig.show()

In [34]:
# Let's look at records with both a mortgage doc and agreement doc and see the percentage
acris['bbl'] = acris['BOROUGH'].astype(str) + acris['BLOCK'].astype(str) + acris['LOT'].astype(str)

agmt_mtge = acris.loc[
    acris['DOC_TYPE'].isin(['MTGE', 'AGMT']), ['bbl', 'DOCUMENT_TYPE', 'DOCUMENT_AMT']
].pivot_table(
    index=['bbl'], 
    columns=['DOCUMENT_TYPE'], 
    values=['DOCUMENT_AMT']
).dropna()

agmt_mtge = agmt_mtge.loc[(agmt_mtge[('DOCUMENT_AMT', 'MORTGAGE')] > 0) & (agmt_mtge[('DOCUMENT_AMT', 'AGREEMENT')] > 0)]
agmt_mtge[('DOCUMENT_AMT', 'PCT')] = agmt_mtge[('DOCUMENT_AMT', 'MORTGAGE')] / agmt_mtge[('DOCUMENT_AMT', 'AGREEMENT')]

In [35]:
px.histogram(agmt_mtge.loc[(agmt_mtge[('DOCUMENT_AMT', 'PCT')] < 1), ('DOCUMENT_AMT', 'PCT')].values, title='Mortgage / Agreement Amount Percentage')